In [17]:
import pandas as pd
import os

In [18]:
DATA_DIR = "../data"
PROCESSED_DIR = "../processed/"
FACET_DIR = "home_values/"
FULL_DATA_DIR_PATH = os.path.join(DATA_DIR, FACET_DIR)
FULL_PROCESSED_DIR_PATH = os.path.join(PROCESSED_DIR, FACET_DIR)

In [19]:
# base cols RegionID,SizeRank,RegionName,RegionType,StateName

data_frames = []

for filename in os.listdir(FULL_DATA_DIR_PATH):
    if filename.endswith(".csv"):
        print("processing " + filename)
        cur_df = pd.read_csv(os.path.join(FULL_DATA_DIR_PATH, filename))
        exclude_columns = [
            "RegionID",
            "SizeRank",
            "RegionName",
            "RegionType",
            "StateName",
            "Bedroom Count",
            "Home Type",
        ]

        if "Zip" in filename:
            continue
        if "Neighborhood" in filename:
            continue
        if "City" in filename:
            continue
        if "Metro" in filename:
            continue
        if "County" in filename:
            continue

        if "City" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Bedroom Count",
                "Home Type",
                # City Specific
                "State",
                "Metro",
                "CountyName",
            ]
        elif "Zip" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Bedroom Count",
                "Home Type",
                # Zip Specific
                "State",
                "City",
                "Metro",
                "CountyName",
            ]
        elif "County" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Bedroom Count",
                "Home Type",
                # County Specific
                "State",
                "Metro",
                "StateCodeFIPS",
                "MunicipalCodeFIPS",
            ]
        elif "Neighborhood" in filename:
            exclude_columns = [
                "RegionID",
                "SizeRank",
                "RegionName",
                "RegionType",
                "StateName",
                "Bedroom Count",
                "Home Type",
                # Neighborhood Specific
                "State",
                "City",
                "Metro",
                "CountyName",
            ]

        if "_bdrmcnt_1_" in filename:
            cur_df["Bedroom Count"] = "1-Bedrooms"
        elif "_bdrmcnt_2_" in filename:
            cur_df["Bedroom Count"] = "2-Bedrooms"
        elif "_bdrmcnt_3_" in filename:
            cur_df["Bedroom Count"] = "3-Bedrooms"
        elif "_bdrmcnt_4_" in filename:
            cur_df["Bedroom Count"] = "4 Bedrooms"
        elif "_bdrmcnt_5_" in filename:
            cur_df["Bedroom Count"] = "5+ Bedrooms"
        else:
            cur_df["Bedroom Count"] = "All Bedrooms"

        if "_uc_sfr_" in filename:
            cur_df["Home Type"] = "SFR"
        elif "_uc_sfrcondo_" in filename:
            cur_df["Home Type"] = "all homes (SFR/condo)"
        elif "_uc_condo_" in filename:
            cur_df["Home Type"] = "condo"

        # Identify columns to pivot
        columns_to_pivot = [col for col in cur_df.columns if col not in exclude_columns]

        smoothed = "_sm_" in filename
        seasonally_adjusted = "_sa_" in filename

        if "_tier_0.33_0.67_" in filename:
            col_name = "Mid Tier ZHVI"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )
        elif "_tier_0.0_0.33_" in filename:
            col_name = "Bottom Tier ZHVI"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )
        elif "_tier_0.67_1.0_" in filename:
            col_name = "Top Tier ZHVI"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )
        else:
            col_name = "ZHVI"
            if smoothed:
                col_name += " (Smoothed)"
            if seasonally_adjusted:
                col_name += " (Seasonally Adjusted)"

            cur_df = pd.melt(
                cur_df,
                id_vars=exclude_columns,
                value_vars=columns_to_pivot,
                var_name="Date",
                value_name=col_name,
            )

        cur_df["StateName"] = cur_df["StateName"].astype(str)
        cur_df["RegionName"] = cur_df["RegionName"].astype(str)

        data_frames.append(cur_df)


def get_combined_df(data_frames):
    combined_df = None
    if len(data_frames) > 1:
        # iterate over dataframes and merge or concat
        combined_df = data_frames[0]
        for i in range(1, len(data_frames)):
            print(i)
            print(len(data_frames))
            cur_df = data_frames[i]
            combined_df = pd.merge(
                combined_df,
                cur_df,
                on=[
                    "RegionID",
                    "SizeRank",
                    "RegionName",
                    "RegionType",
                    "StateName",
                    "Bedroom Count",
                    "Home Type",
                    "Date",
                ],
                how="outer",
                suffixes=("", "_" + str(i)),
            )
    elif len(data_frames) == 1:
        combined_df = data_frames[0]

    return combined_df


combined_df = get_combined_df(data_frames)
combined_df

processing City_zhvi_uc_condo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Metro_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing County_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing Metro_zhvi_bdrmcnt_2_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_uc_sfr_tier_0.33_0.67_sm_sa_month.csv
processing Neighborhood_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing State_zhvi_uc_sfr_tier_0.33_0.67_sm_sa_month.csv
processing County_zhvi_uc_condo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_bdrmcnt_4_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing State_zhvi_bdrmcnt_5_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing Zip_zhvi_bdrmcnt_2_uc_sfrcondo_tier_0.33_0.67_sm_sa_month.csv
processing City_zhvi_uc_sfrcondo_tier_0.67_1.0_sm_sa_month.csv
processing Zip_zhvi_uc_condo_tier_0.33_0.67_

RegionID  SizeRank RegionName RegionType StateName Bedroom Count  \
0              3        48     Alaska      state       nan    1-Bedrooms   
1              3        48     Alaska      state       nan    1-Bedrooms   
2              3        48     Alaska      state       nan    1-Bedrooms   
3              3        48     Alaska      state       nan    1-Bedrooms   
4              3        48     Alaska      state       nan    1-Bedrooms   
...          ...       ...        ...        ...       ...           ...   
117907        62        51    Wyoming      state       nan  All Bedrooms   
117908        62        51    Wyoming      state       nan  All Bedrooms   
117909        62        51    Wyoming      state       nan  All Bedrooms   
117910        62        51    Wyoming      state       nan  All Bedrooms   
117911        62        51    Wyoming      state       nan  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_1  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)_2  \
0                                                    NaN   
1                                                    NaN   
2                                                    NaN   
3                                                    NaN   
4                                                    NaN   
...                                                  ...   
117907                                               NaN   
117908                                               NaN   
117909                                               NaN   
117910                                               NaN   
117911                                               NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                              

In [20]:
# iterate over rows of combined df and coalesce column values across columns that start with "Median Sale Price"
columns_to_coalesce = ["ZHVI", "Mid Tier ZHVI", "Bottom Tier ZHVI", "Top Tier ZHVI"]

for column_to_coalesce in columns_to_coalesce:
    print(column_to_coalesce)
    for index, row in combined_df.iterrows():
        for col in combined_df.columns:
            if column_to_coalesce in col and "_" in col:
                if not pd.isna(row[col]):
                    combined_df.at[index, column_to_coalesce] = row[col]

# remove columns with underscores
combined_df = combined_df[[col for col in combined_df.columns if "_" not in col]]


combined_df

ZHVI
Mid Tier ZHVI
Bottom Tier ZHVI
Top Tier ZHVI


RegionID  SizeRank RegionName RegionType StateName Bedroom Count  \
0              3        48     Alaska      state       nan    1-Bedrooms   
1              3        48     Alaska      state       nan    1-Bedrooms   
2              3        48     Alaska      state       nan    1-Bedrooms   
3              3        48     Alaska      state       nan    1-Bedrooms   
4              3        48     Alaska      state       nan    1-Bedrooms   
...          ...       ...        ...        ...       ...           ...   
117907        62        51    Wyoming      state       nan  All Bedrooms   
117908        62        51    Wyoming      state       nan  All Bedrooms   
117909        62        51    Wyoming      state       nan  All Bedrooms   
117910        62        51    Wyoming      state       nan  All Bedrooms   
117911        62        51    Wyoming      state       nan  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
117907                                                NaN   
117908                                                NaN   
117909                                                NaN   
117910                                                NaN   
117911                                                NaN   

        Top Tier ZHVI (Smoothed) (Seasonally Adjusted)           ZHVI  \
0                                                  NaN   81310.639504   
1                                                  NaN   80419.761984   
2                                                  NaN   80480.449461   
3                                                  NaN   79799.206525   
4                                                  NaN   79666.469861   
...                                                ...            ...   
117907                                             NaN  486974.735908   
117908                                             NaN  485847.539614   
117909                                             NaN  484223.885775   
117910                                             NaN  481522.403338   
117911                                             NaN  481181.718200   

        Mid Tier ZHVI  
0        81310.639504  
1        80419.761984  
2        80480.449461  
3        79799.206525  
4        79666.469861  
...               ...  
117907  486974.735908  
117908  485847.539614  
117909  484223.885775  
117910 

In [21]:
final_df = combined_df

for index, row in final_df.iterrows():
    if row["RegionType"] == "city":
        final_df.at[index, "City"] = row["RegionName"]
    elif row["RegionType"] == "county":
        final_df.at[index, "County"] = row["RegionName"]
    if row["RegionType"] == "state":
        final_df.at[index, "StateName"] = row["RegionName"]

# coalesce State and StateName columns
# final_df["State"] = final_df["State"].combine_first(final_df["StateName"])
# final_df["County"] = final_df["County"].combine_first(final_df["CountyName"])

# final_df = final_df.drop(
#     columns=[
#         "StateName",
#         # "CountyName"
#     ]
# )
final_df

RegionID  SizeRank RegionName RegionType StateName Bedroom Count  \
0              3        48     Alaska      state    Alaska    1-Bedrooms   
1              3        48     Alaska      state    Alaska    1-Bedrooms   
2              3        48     Alaska      state    Alaska    1-Bedrooms   
3              3        48     Alaska      state    Alaska    1-Bedrooms   
4              3        48     Alaska      state    Alaska    1-Bedrooms   
...          ...       ...        ...        ...       ...           ...   
117907        62        51    Wyoming      state   Wyoming  All Bedrooms   
117908        62        51    Wyoming      state   Wyoming  All Bedrooms   
117909        62        51    Wyoming      state   Wyoming  All Bedrooms   
117910        62        51    Wyoming      state   Wyoming  All Bedrooms   
117911        62        51    Wyoming      state   Wyoming  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
117907                                                NaN   
117908                                                NaN   
117909                                                NaN   
117910                                                NaN   
117911                                                NaN   

        Top Tier ZHVI (Smoothed) (Seasonally Adjusted)           ZHVI  \
0                                                  NaN   81310.639504   
1                                                  NaN   80419.761984   
2                                                  NaN   80480.449461   
3                                                  NaN   79799.206525   
4                                                  NaN   79666.469861   
...                                                ...            ...   
117907                                             NaN  486974.735908   
117908                                             NaN  485847.539614   
117909                                             NaN  484223.885775   
117910                                             NaN  481522.403338   
117911                                             NaN  481181.718200   

        Mid Tier ZHVI  
0        81310.639504  
1        80419.761984  
2        80480.449461  
3        79799.206525  
4        79666.469861  
...               ...  
117907  486974.735908  
117908  485847.539614  
117909  484223.885775  
117910 

In [22]:
final_df = final_df.rename(
    columns={
        "RegionID": "Region ID",
        "SizeRank": "Size Rank",
        "RegionName": "Region",
        "RegionType": "Region Type",
        "StateCodeFIPS": "State Code FIPS",
        "StateName": "State",
        "MunicipalCodeFIPS": "Municipal Code FIPS",
    }
)

final_df

Region ID  Size Rank   Region Region Type    State Bedroom Count  \
0               3         48   Alaska       state   Alaska    1-Bedrooms   
1               3         48   Alaska       state   Alaska    1-Bedrooms   
2               3         48   Alaska       state   Alaska    1-Bedrooms   
3               3         48   Alaska       state   Alaska    1-Bedrooms   
4               3         48   Alaska       state   Alaska    1-Bedrooms   
...           ...        ...      ...         ...      ...           ...   
117907         62         51  Wyoming       state  Wyoming  All Bedrooms   
117908         62         51  Wyoming       state  Wyoming  All Bedrooms   
117909         62         51  Wyoming       state  Wyoming  All Bedrooms   
117910         62         51  Wyoming       state  Wyoming  All Bedrooms   
117911         62         51  Wyoming       state  Wyoming  All Bedrooms   

                    Home Type        Date  \
0       all homes (SFR/condo)  2000-01-31   
1       all homes (SFR/condo)  2000-02-29   
2       all homes (SFR/condo)  2000-03-31   
3       all homes (SFR/condo)  2000-04-30   
4       all homes (SFR/condo)  2000-05-31   
...                       ...         ...   
117907                  condo  2023-09-30   
117908                  condo  2023-10-31   
117909                  condo  2023-11-30   
117910                  condo  2023-12-31   
117911                  condo  2024-01-31   

        Mid Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                  NaN   
1                                                  NaN   
2                                                  NaN   
3                                                  NaN   
4                                                  NaN   
...                                                ...   
117907                                             NaN   
117908                                             NaN   
117909                                             NaN   
117910                                             NaN   
117911                                             NaN   

        Bottom Tier ZHVI (Smoothed) (Seasonally Adjusted)  \
0                                                     NaN   
1                                                     NaN   
2                                                     NaN   
3                                                     NaN   
4                                                     NaN   
...                                                   ...   
117907                                                NaN   
117908                                                NaN   
117909                                                NaN   
117910                                                NaN   
117911                                                NaN   

        Top Tier ZHVI (Smoothed) (Seasonally Adjusted)           ZHVI  \
0                                                  NaN   81310.639504   
1                                                  NaN   80419.761984   
2                                                  NaN   80480.449461   
3                                                  NaN   79799.206525   
4                                                  NaN   79666.469861   
...                                                ...            ...   
117907                                             NaN  486974.735908   
117908                                             NaN  485847.539614   
117909                                             NaN  484223.885775   
117910                                             NaN  481522.403338   
117911                                             NaN  481181.718200   

        Mid Tier ZHVI  
0        81310.639504  
1        80419.761984  
2        80480.449461  
3        79799.206525  
4        79666.469861  
...               ...  
117907  486974.735908  
117908  485847.539614  
117909  484223.885775  
117910 

In [23]:
if not os.path.exists(FULL_PROCESSED_DIR_PATH):
    os.makedirs(FULL_PROCESSED_DIR_PATH)

final_df.to_json(FULL_PROCESSED_DIR_PATH + "final.jsonl", orient="records", lines=True)